# Check pnl across trades and positions

* Compare trade pnl between two subgraphs
* Compare position pnl between two subgraphs


In [1]:
import os
from copy import deepcopy
from datetime import datetime
import asyncio
import requests
import pandas as pd
import numpy as np
import json
from gql import Client, gql
from gql.transport.aiohttp import AIOHTTPTransport
from decimal import Decimal
from dotenv import load_dotenv
import plotly.io as pio
import plotly.express as px

load_dotenv()

pio.renderers.default = 'notebook'


In [2]:
## constants
INFURA_KEY = os.getenv('INFURA_KEY')

# mainnet
OLD_SUBGRAPH_ENDPOINT = 'https://api.thegraph.com/subgraphs/name/kwenta/optimism-perps'
SUBGRAPH_ENDPOINT = 'https://api.thegraph.com/subgraphs/name/tburm/optimism-perps'
RPC_ENDPOINT = f'https://optimism-mainnet.infura.io/v3/{INFURA_KEY}'

# testnet
# SUBGRAPH_ENDPOINT = 'https://api.thegraph.com/subgraphs/name/kwenta/optimism-goerli-perps'
# RPC_ENDPOINT = f'https://optimism-kovan.infura.io/v3/{INFURA_KEY}'


In [3]:
# functions
convertDecimals = lambda x: Decimal(x) / Decimal(10**18)
convertBytes = lambda x: bytearray.fromhex(x[2:]).decode().replace('\x00', '')

def clean_df(df, decimal_cols=[], bytes_cols=[]):
    for col in decimal_cols:
        if col in df.columns:
            df[col] = df[col].apply(convertDecimals)
        else:
            print(f"{col} not in DataFrame")
    for col in bytes_cols:
        if col in df.columns:
            df[col] = df[col].apply(convertBytes)
        else:
            print(f"{col} not in DataFrame")
    return df

async def run_query(query, params, endpoint=SUBGRAPH_ENDPOINT):
    transport = AIOHTTPTransport(url=endpoint)

    async with Client(
        transport=transport,
        fetch_schema_from_transport=True,
    ) as session:

        # Execute single query
        query = query

        result = await session.execute(query, variable_values=params)
        df = pd.DataFrame(result)
        return df

async def run_recursive_query(query, params, accessor, endpoint=SUBGRAPH_ENDPOINT):
  transport = AIOHTTPTransport(url=endpoint)

  async with Client(
      transport=transport,
      fetch_schema_from_transport=True,
  ) as session:
    done_fetching = False
    all_results = []
    while not done_fetching:
      result = await session.execute(query, variable_values=params)
      if len(result[accessor]) > 0:
        all_results.extend(result[accessor])
        params['last_id'] = all_results[-1]['id']
      else:
        done_fetching = True
    
    df = pd.DataFrame(all_results)
    return df


In [4]:
position_query = gql("""
query positions(
    $last_id: ID!
  ) {
    futuresPositions(
      where: {
        id_gt: $last_id
      }
      # block: {number: 74087200}
      first: 1000
     ) {
      id
      account
      asset
      initialMargin
      size
      entryPrice
      avgEntryPrice
      lastPrice
      exitPrice
      pnl
      pnlWithFeesPaid
      openTimestamp
      closeTimestamp
      feesPaid
      netFunding
      isLiquidated
      isOpen
      margin
      netTransfers
      totalDeposits
      totalVolume
      lastTxHash
    }  
}
""")

trade_query = gql("""
query trades(
    $last_id: ID!
  ) {
    futuresTrades(
      where: {
        id_gt: $last_id
      }
      first: 1000
     ) {
      id
      account
      timestamp
      asset
      marketKey
      orderType
      price
      margin
      positionId
      feesPaid
      pnl
      size
      positionSize
      positionClosed
    }  
}
""")

stats_query = gql("""
query stats(
    $last_id: ID!
  ) {
    futuresStats(
      where: {
        id_gt: $last_id
      }
      first: 1000
     ) {
      id
      account
      totalTrades
      totalVolume
      feesPaid
      pnl
      pnlWithFeesPaid
      liquidations
    }  
}
""")


### Run a query

In [5]:
position_params = {
    'last_id': ''
}

position_cols = [
    'avgEntryPrice',
    'entryPrice',
    'exitPrice',
    'feesPaid',
    'initialMargin',
    'lastPrice',
    'margin',
    'netFunding',
    'netTransfers',
    'pnl',
    'pnlWithFeesPaid',
    'size',
    'totalDeposits',
    'totalVolume'
]

position_bytes_cols = ['asset']

df_position = await run_recursive_query(position_query, position_params, 'futuresPositions')
df_position = df_position.replace({None: np.nan})
df_position = clean_df(df_position, decimal_cols=position_cols, bytes_cols=position_bytes_cols)
df_position['netPnl'] = df_position['pnl'] - df_position['feesPaid']


In [6]:
df_position

id  \
0        0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x0   
1        0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x1   
2       0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x10   
3      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x100   
4      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x101   
...                                                 ...   
11385    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xb   
11386    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xc   
11387    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xd   
11388    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xe   
11389    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xf   

                                          account  asset  \
0      0x8feafd5e0fcefdd2624906c0f913d563306aae17  MATIC   
1      0x8feafd5e0fcefdd2624906c0f913d563306aae17  MATIC   
2      0xc8728ae130381eb77fc9a8b715564b00e83e19df  MATIC   
3      0x2c23f12195077bee4ac4f7d598af30904a5fbf91  MATIC   
4      0xd8e80c06f9f3a41c85cad28117e01ebd50fd535e  MATIC   
...                                           ...    ...   
11385  0x78f214cf1287b5c97df55a285e885b09c0d43e3d    XAG   
11386  0x88747e96c045e71b357ce0b75597492beaa1fb8f    XAG   
11387  0x11ba886f23173da913aa3dbc51492e8080a781ac    XAG   
11388  0x41dbd3a603adfb85c47fee7cf999d32bcc36a4f1    XAG   
11389  0xefabf4585217f458d54b6b5225a9c7a2222bd704    XAG   

                initialMargin size             entryPrice  \
0       77.199529739466510105    0                  1.336   
1       75.199529739466510105    0   1.340312948674674971   
2      197.498040648137408231    0   1.252917520139616653   
3                          98    0   1.271783672974139673   
4      777.321876625415779658    0   1.257577965021184482   
...                       ...  ...                    ...   
11385  162.739186100680223994    0  21.695059131724097826   
11386                      98    0  21.728833842533239428   
11387                    4998    0  21.482620917757409705   
11388  183.427032240973901673    0  21.728166360389986619   
11389                     588    0  20.818505592475501069   

               avgEntryPrice              lastPrice              exitPrice  \
0                      1.336   1.030985589554772303                    NaN   
1       1.340312948674674971   1.341738286882998216   1.341738286882998216   
2       1.252917520139616653   1.215543235997026069   1.215543235997026069   
3       1.271783672974139673   1.268341831466371221   1.268341831466371221   
4       1.257577965021184482   1.205252195554925268   1.205252195554925268   
...                      ...                    ...                    ...   
11385  21.695059131724097826  21.635837322225261266  21.635837322225261266   
11386  21.728833842533239428  21.580583270495936189  21.580583270495936189   
11387  21.482620917757409705   21.82713009230149882   21.82713009230149882   
11388  21.728166360389986619  21.816099329108998862  21.816099329108998862   
11389  20.818505592475501069   20.08498698104437367   20.08498698104437367   

                           pnl  ...               feesPaid  \
0                            0  ...                      0   
1         2.052092628903229758  ...   7.861001237100389934   
2        29.769574101247450474  ...    5.57295374788655442   
3         6.767650966258712392  ...   8.993264259656970653   
4       210.365882266396886773  ...  13.943417100998227914   
...                        ...  ...                    ...   
11385   -15.956808702549099059  ...    7.75206860911845269   
11386   -13.642729241618423108  ...   4.598513203653544012   
11387   641.506744317628356061  ...  16.064916305069556019   
11388    14.574525202046228121  ...   5.081863514639043735   
11389  -203.805505645917437276  ...  11.714923500189632022   

                  netFunding isLiquidated isOpen                   margin  \
0                          0        False   True  6056.019382035991456336   
1          -8.08234215782E-7        False  False    71

In [7]:
trade_params = {
    'last_id': ''
}

trade_decimal_cols = [
    'price',
    'margin',
    'feesPaid',
    'pnl',
    'size',
    'positionSize',
]

trade_bytes_cols = [
    'marketKey',
    'asset',
]

df_trade = await run_recursive_query(trade_query, trade_params, 'futuresTrades')
df_trade = df_trade.replace({None: np.nan})
df_trade = clean_df(df_trade, decimal_cols=trade_decimal_cols, bytes_cols=trade_bytes_cols)
df_trade['netPnl'] = df_trade['pnl'] - df_trade['feesPaid']


In [8]:
df_trade


id  \
0      0x0000709c04c4a1f048371ca2e2641740b161f24db3da...   
1      0x00028b72733b86a53c61e5ed7a842263945d64c6c813...   
2      0x000386002a2352898e1cd3992ebaf0d81917323fc32e...   
3      0x0003d5401b4c7a8a1feb9e8ea750336e6df42b5cd3ff...   
4      0x000ad64e851c16a8d33b9dcfa80e94ae3952fe84223e...   
...                                                  ...   
31445  0xfff4746b170ebf38b40fd4d3036de9d70795abf2de15...   
31446  0xfff8f635b096ed1d76711a1c1e8c295774e4a71d63a1...   
31447  0xfff96e959bc63b043de5c88eb69570a307f454257cf7...   
31448  0xfffa05badf2f0d88015112586edf17653224a4d9c9e1...   
31449  0xfffd7f82207d4ce1a02a801128141a230e63f203bd2f...   

                                          account   timestamp  asset  \
0      0x02bee0a17903cc1f2f48b4514ec23aae547fe4a3  1678414645     OP   
1      0x70b3d1ff337bcceeb3e2cf5b05efbffc50af87d7  1677087956  MATIC   
2      0x9d4e2ddf02f524c3c4cb8ac4fb99af1ebf08afce  1678444220    FTM   
3      0x50d36f27872f637ec9ecb4eedff300df44a608ab  1673640747   sETH   
4      0x6fb737d1ebb73cda6cfa36fd16d9273065d1b084  1676621493     OP   
...                                           ...         ...    ...   
31445  0xc814d2ef6d893568c74cd969eb6f72a62fc261f7  1678128866   sETH   
31446  0xb726916fb98efe5f3d167c26dfe32c5c4f869d84  1678304491   DYDX   
31447  0xc31b0df48319a83eeffd9280f3f29707ec950092  1671649414   sETH   
31448  0x018439894b681cc2aaddb613a425a1cfa6e59c29  1677885382   sETH   
31449  0xc15ab8dd7daeea5f1aa3b56507cac8a877e21b15  1677353373    APE   

        marketKey        orderType                    price  \
0         sOPPERP  DelayedOffchain     2.213578991306346108   
1      sMATICPERP  DelayedOffchain     1.346733270313601043   
2        sFTMPERP  DelayedOffchain     0.308018301447319327   
3        sETHPERP  DelayedOffchain  1420.509945340577467893   
4         sOPPERP  DelayedOffchain     2.719976157048370677   
...           ...              ...                      ...   
31445    sETHPERP  DelayedOffchain  1576.072080636698071397   
31446   sDYDXPERP  DelayedOffchain     2.057995714535357106   
31447    sETHPERP  DelayedOffchain  1210.561005015049885549   
31448    sETHPERP  DelayedOffchain  1573.947671908464662927   
31449    sAPEPERP  DelayedOffchain     4.902165109390658502   

                        margin  \
0       358.166388968351018287   
1        1047.5773280909209386   
2       1214.65905592211859337   
3        83.803545657223511638   
4                           98   
...                        ...   
31445   784.658729173398341707   
31446   237.333070975315446145   
31447    49.922118336338367668   
31448  6044.772262963300594611   
31449   518.803947978414985064   

                                             positionId  \
0      0x442b69937a0daf9d46439a71567fabe6cb69fbaf-0x654   
1       0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0xc4   
2       0xc18f85a6dd3bcd0516a1ca08d3b1f0a4e191a2c4-0xc7   
3      0x2b3bb4c683bfc5239b029131eef3b1d214478d93-0x26b   
4      0x442b69937a0daf9d46439a71567fabe6cb69fbaf-0x10b   
...                                                 ...   
31445  0x2b3bb4c683bfc5239b029131eef3b1d214478d93-0xf84   
31446  0x139f94e4f0e1101c1464a321cba815c34d58b5d9-0x17c   
31447   0x2b3bb4c683bfc5239b029131eef3b1d214478d93-0x20   
31448  0x2b3bb4c683bfc5239b029131eef3b1d214478d93-0xfee   
31449   0x5b6beb79e959aac2659bee60fe0d0885468bf886-0x37   

                    feesPaid                     pnl                  size  \
0      17.112465583134553901  -34.997997791322001114            -4551.4423   
1       9.397554354752353737  215.552868807478393106             6866.2022   
2      29.337790148923313592                       0           -59169.1901   
3       3.128026947594952567   -0.142862529594830699               -1.5882   
4       2.414277528497919551                       0             -101.5395   
...                      ...                     ...                   ...   
31445    5.52590965519638909   25.7475738474820

In [9]:
stat_params = {
    'last_id': ''
}

stat_decimal_cols = [
    'pnl',
    'feesPaid',
    'pnlWithFeesPaid'
]

df_stat = await run_recursive_query(stats_query, stat_params, 'futuresStats')
df_stat = df_stat.replace({None: np.nan})
df_stat = clean_df(df_stat, decimal_cols=stat_decimal_cols)
df_stat


id  \
0     0x000741def5c59bead2b2f6be2d35fc4145e39e6b   
1     0x0028112a819a2fea8802b27c8abd755152f548ba   
2     0x0045fa93dedb0af02956f7d7c306b34263688872   
3     0x0046e6b678371f3576408873b3941b9ab10e3c72   
4     0x0099560ec05a765a6b95443d4039ce1daf24f805   
...                                          ...   
2318  0xff714698695caab8c83061bb9732967a50730570   
2319  0xff789ab6730c22da1e095645836cb70eaf5cfc51   
2320  0xff9e5e8cb270d80c2eb6059c6b0d70a9aec96922   
2321  0xffd3003a187d9951e49bda206f32a6e765360427   
2322  0xffff14c6bc3a2d03a500885bb824f81d3b1e23cf   

                                         account totalTrades  \
0     0x000741def5c59bead2b2f6be2d35fc4145e39e6b           4   
1     0x0028112a819a2fea8802b27c8abd755152f548ba           0   
2     0x0045fa93dedb0af02956f7d7c306b34263688872          22   
3     0x0046e6b678371f3576408873b3941b9ab10e3c72           4   
4     0x0099560ec05a765a6b95443d4039ce1daf24f805           7   
...                                          ...         ...   
2318  0xff714698695caab8c83061bb9732967a50730570           2   
2319  0xff789ab6730c22da1e095645836cb70eaf5cfc51           0   
2320  0xff9e5e8cb270d80c2eb6059c6b0d70a9aec96922           6   
2321  0xffd3003a187d9951e49bda206f32a6e765360427           0   
2322  0xffff14c6bc3a2d03a500885bb824f81d3b1e23cf           4   

                  totalVolume                feesPaid                     pnl  \
0     41911171609596478509050  875.447775250601310784                       0   
1                           0                       0                       0   
2      5943269272578803358910   54.800306441032211018  -53.897165827339280358   
3      2243356863904652944833   14.328902650518394115    0.158035901794500817   
4     87241243160109805784710  335.323834259563303579                       0   
...                       ...                     ...                     ...   
2318    299851768801504608411    2.224866322280623873   -0.091948537070266261   
2319                        0                       0                       0   
2320  30143493030746285378356    3.601702842277823946   44.513285891069027085   
2321                        0                       0                       0   
2322   2335451078632487990783    9.751538332510166579    0.012533838874905188   

              pnlWithFeesPaid liquidations  
0     -873.447775250601310784            0  
1                           0            0  
2     -106.697472268371491376            0  
3      -14.170866748723893298            0  
4     -333.323834259563303579            0  
...                       ...          ...  
2318    -2.316814859350890134            0  
2319                        0            0  
2320    40.911583048791203139            0  
2321                        0            0  
2322    -9.739004493635261391            0  

[2323 rows x 8 columns]

## Trades vs Positions

In [10]:
trade_pnl = df_trade.groupby('positionId')[['pnl', 'netPnl']].sum().reset_index()

df_pnl = df_position[['id', 'pnl', 'netPnl', 'asset', 'isLiquidated', 'isOpen']].merge(trade_pnl, left_on='id', right_on='positionId', suffixes=['_position', '_trade'])
df_pnl['diff'] = df_pnl['netPnl_trade'] - df_pnl['netPnl_position']
df_pnl



id  \
0        0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x1   
1       0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x10   
2      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x100   
3      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x101   
4      0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x102   
...                                                 ...   
11362    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xb   
11363    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xc   
11364    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xd   
11365    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xe   
11366    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xf   

                  pnl_position          netPnl_position  asset  isLiquidated  \
0         2.052092628903229758    -5.808908608197160176  MATIC         False   
1        29.769574101247450474    24.196620353360896054  MATIC         False   
2         6.767650966258712392    -2.225613293398258261  MATIC         False   
3       210.365882266396886773   196.422465165398658859  MATIC         False   
4      -715.337868864416570932  -745.233983948528637837  MATIC         False   
...                        ...                      ...    ...           ...   
11362   -15.956808702549099059   -23.708877311667551749    XAG         False   
11363   -13.642729241618423108   -18.241242445271967120    XAG         False   
11364   641.506744317628356061   625.441828012558800042    XAG         False   
11365    14.574525202046228121     9.492661687407184386    XAG         False   
11366  -203.805505645917437276  -215.520429146107069298    XAG         False   

       isOpen                                        positionId  \
0       False    0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x1   
1       False   0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x10   
2       False  0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x100   
3       False  0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x101   
4       False  0x074b8f19fc91d6b2eb51143e1f186ca0ddb88042-0x102   
...       ...                                               ...   
11362   False    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xb   
11363   False    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xc   
11364   False    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xd   
11365   False    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xe   
11366   False    0xdcb8438c979fa030581314e5a5df42bbfed744a0-0xf   

                     pnl_trade             netPnl_trade   diff  
0         2.052092628903229758    -5.808908608197160176  0E-18  
1        29.769574101247450474    24.196620353360896054  0E-18  
2         6.767650966258712392    -2.225613293398258261  0E-18  
3       210.365882266396886773   196.422465165398658859  0E-18  
4      -715.337868864416570932  -745.233983948528637837  0E-18  
...                        ...                      ...    ...  
11362   -15.956808702549099059   -23.708877311667551749  0E-18  
11363   -13.642729241618423108   -18.241242445271967120  0E-18  
11364   641.506744317628356061   625.441828012558800042  0E-18  
11365    14.574525202046228121     9.492661687407184386  0E-18  
11366  -203.805505645917437276  -215.520429146107069298  0E-18  

[11367 rows x 10 columns]

In [11]:
df_pnl.loc[(df_pnl['netPnl_position'] != df_pnl['netPnl_trade']), :].sort_values('diff', ascending=True)

Empty DataFrame
Columns: [id, pnl_position, netPnl_position, asset, isLiquidated, isOpen, positionId, pnl_trade, netPnl_trade, diff]
Index: []

In [12]:
df_pnl.loc[(df_pnl['pnl_position'] != df_pnl['pnl_trade']), :].sort_values('diff', ascending=True)

Empty DataFrame
Columns: [id, pnl_position, netPnl_position, asset, isLiquidated, isOpen, positionId, pnl_trade, netPnl_trade, diff]
Index: []

## Compare position and trader pnl

In [13]:
df_position_agg = df_position.groupby('account')[['pnl', 'pnlWithFeesPaid']].sum().reset_index()
df_trade_agg = df_trade.groupby('account')[['pnl']].sum().reset_index()

df_compare = df_stat[['account', 'pnl', 'pnlWithFeesPaid', 'liquidations']].merge(df_position_agg, on='account', suffixes=['_stat', '_position'])
df_compare = df_compare.merge(df_trade_agg, on='account', suffixes=['', '_trade'])

In [14]:
df_compare

account                  pnl_stat  \
0     0x000741def5c59bead2b2f6be2d35fc4145e39e6b                         0   
1     0x0045fa93dedb0af02956f7d7c306b34263688872    -53.897165827339280358   
2     0x0046e6b678371f3576408873b3941b9ab10e3c72      0.158035901794500817   
3     0x0099560ec05a765a6b95443d4039ce1daf24f805                         0   
4     0x00a25c455636cc01bffcb717db900a6d4c767a8a  -7064.527920158989496476   
...                                          ...                       ...   
2027  0xff5144b6d2aaa53eade50c308c23d5c2151582d2   -144.929517124945227848   
2028  0xff6f84ce85166396d1402d14721ac350634a5d4b      1.208595124603055855   
2029  0xff714698695caab8c83061bb9732967a50730570     -0.091948537070266261   
2030  0xff9e5e8cb270d80c2eb6059c6b0d70a9aec96922     44.513285891069027085   
2031  0xffff14c6bc3a2d03a500885bb824f81d3b1e23cf      0.012533838874905188   

           pnlWithFeesPaid_stat liquidations              pnl_position  \
0       -873.447775250601310784            0                         0   
1       -106.697472268371491376            0    -53.897165827339280358   
2        -14.170866748723893298            0      0.158035901794500817   
3       -333.323834259563303579            0                         0   
4     -14800.022697126097450739            0  -7064.527920158989496476   
...                         ...          ...                       ...   
2027    -174.100353362168086913            2   -144.929517124945227848   
2028       -3.47574880960140501            0      1.208595124603055855   
2029      -2.316814859350890134            0     -0.091948537070266261   
2030      40.911583048791203139            0     44.513285891069027085   
2031      -9.739004493635261391            0      0.012533838874905188   

       pnlWithFeesPaid_position                       pnl  
0       -873.447775250601310784                         0  
1        -90.697472268371491376    -53.897165827339280358  
2        -14.170866748723893298      0.158035901794500817  
3       -333.323834259563303579                         0  
4     -14780.022697126097450739  -7064.527920158989496476  
...                         ...                       ...  
2027    -170.100353362168086913   -144.929517124945227848  
2028      -1.475748809601405010      1.208595124603055855  
2029      -1.316814859350890134     -0.091948537070266261  
2030      46.911583048791203139     44.513285891069027085  
2031      -5.739004493635261391      0.012533838874905188  

[2032 rows x 7 columns]

In [15]:
df_compare[(df_compare['pnl_stat'] != df_compare['pnl_position'])]

Empty DataFrame
Columns: [account, pnl_stat, pnlWithFeesPaid_stat, liquidations, pnl_position, pnlWithFeesPaid_position, pnl]
Index: []

In [16]:
df_compare[(df_compare['pnl_stat'] != df_compare['pnl'])]


Empty DataFrame
Columns: [account, pnl_stat, pnlWithFeesPaid_stat, liquidations, pnl_position, pnlWithFeesPaid_position, pnl]
Index: []

## Get a specific position

In [17]:
position_id = '0x111babcdd66b1b60a20152a2d3d06d36f8b5703c-0x7f'


In [18]:
df_trade[df_trade['positionId'] == position_id].sort_values('timestamp')


Empty DataFrame
Columns: [id, account, timestamp, asset, marketKey, orderType, price, margin, positionId, feesPaid, pnl, size, positionSize, positionClosed, netPnl]
Index: []

In [19]:
df_position[df_position['id'] == position_id]


Empty DataFrame
Columns: [id, account, asset, initialMargin, size, entryPrice, avgEntryPrice, lastPrice, exitPrice, pnl, pnlWithFeesPaid, openTimestamp, closeTimestamp, feesPaid, netFunding, isLiquidated, isOpen, margin, netTransfers, totalDeposits, totalVolume, lastTxHash, netPnl]
Index: []

[0 rows x 23 columns]

In [20]:
df_trade.loc[df_trade['positionId'] == position_id, 'netPnl'].sum()

0

## Get trader

In [21]:
trader = '0x1681Cad31E305874B5A21396E40FA7dC170B2791'.lower()


In [22]:
df_trade.loc[df_trade['account'] == trader, :].sort_values('timestamp')

id  \
7832   0x3fbb627bdd898002889c7d2ce0444b2e29d6aa0a50a9...   
30887  0xfb2a1ff5159d78192c74cc8f1a5028aaf840d2095cf8...   
22050  0xb337cd37dd13c62361dacfb8d8c955ce0cffeba7359a...   
15339  0x7cfdb28c36d0295505554b8565d1b134c5f335489d86...   
7602   0x3dc148b8d834a44e15c438907dfdeb7616f1c2638784...   
...                                                  ...   
7091   0x39a9a365b6489eea28c5a08178b0e6118d036844bf02...   
5624   0x2dcb38e39a368f98c0f3d30560655b52dc741609b505...   
16185  0x840de87da938c3b8a79b83098413195351b5c92e28c4...   
2085   0x10857de80cd08951f81d2718c9134ce00781589f5613...   
8709   0x46a411a7944992b807c39735397dacc698ce81bbf8fb...   

                                          account   timestamp asset marketKey  \
7832   0x1681cad31e305874b5a21396e40fa7dc170b2791  1677113535    OP   sOPPERP   
30887  0x1681cad31e305874b5a21396e40fa7dc170b2791  1677114963    OP   sOPPERP   
22050  0x1681cad31e305874b5a21396e40fa7dc170b2791  1677115555    OP   sOPPERP   
15339  0x1681cad31e305874b5a21396e40fa7dc170b2791  1677115723    OP   sOPPERP   
7602   0x1681cad31e305874b5a21396e40fa7dc170b2791  1677117568    OP   sOPPERP   
...                                           ...         ...   ...       ...   
7091   0x1681cad31e305874b5a21396e40fa7dc170b2791  1677446286  sETH  sETHPERP   
5624   0x1681cad31e305874b5a21396e40fa7dc170b2791  1677446376  sETH  sETHPERP   
16185  0x1681cad31e305874b5a21396e40fa7dc170b2791  1677458512  sETH  sETHPERP   
2085   0x1681cad31e305874b5a21396e40fa7dc170b2791  1677503808  sETH  sETHPERP   
8709   0x1681cad31e305874b5a21396e40fa7dc170b2791  1678135244  sETH  sETHPERP   

             orderType                    price                    margin  \
7832   DelayedOffchain     2.742483291565918274  12132.811078139668205447   
30887  DelayedOffchain     2.744877321366261343  19660.711270143107299557   
22050  DelayedOffchain     2.751664489714393578   20172.80702507197470106   
15339  DelayedOffchain     2.751838190521767399  19869.236359384337876648   
7602   DelayedOffchain     2.756007083249334791  20597.428467644389381177   
...                ...                      ...                       ...   
7091   DelayedOffchain  1648.182427311804008354   44555.16705323421869018   
5624   DelayedOffchain  1648.182509171456408634  44305.591221217554198127   
16185  DelayedOffchain  1636.055999288635818221  59318.245402543241515302   
2085   DelayedOffchain  1647.383999567774008008  53300.702709057081844391   
8709   DelayedOffchain  1563.744085896039067759    122.755856786302913689   

                                             positionId  \
7832   0x442b69937a0daf9d46439a71567fabe6cb69fbaf-0x1ec   
30887  0x442b69937a0daf9d46439a71567fabe6cb69fbaf-0x1ec   
22050  0x442b69937a0daf9d46439a71567fabe6cb69fbaf-0x1ec   
15339  0x442b69937a0daf9d46439a71567fabe6cb69fbaf-0x1f0   
7602   0x442b69937a0daf9d46439a71567fabe6cb69fbaf-0x1f0   
...                                                 ...   
7091   0x2b3bb4c683bfc5239b029131eef3b1d214478d93-0xd26   
5624   0x2b3bb4c683bfc5239b029131eef3b1d214478d93-0xd26   
16185  0x2b3bb4c683bfc5239b029131eef3b1d214478d93-0xd26   
2085   0x2b3bb4c683bfc5239b029131eef3b1d214478d93-0xd26   
8709   0x2b3bb4c683bfc5239b029131eef3b1d214478d93-0xd26   

                     feesPaid                      pnl  \
7832   227.367896457806152764                        0   
30887  227.675601935898782989                        0   
22050  303.570665687636824412   875.000091833533927965   
15339  453.501475148249907077                        0   
7602    11.017553470973167702                        0   
...                       ...                      ...   
7091   249.227364096770601253                        0   
5624   125.613688187859230647                        0   
16185   83.802799964431790911                        0   
2085   824.044615784319229995  -206.681059695158193416   
8709     3.563744085896039067    83.225723171343841665   

                            s

In [23]:
df_position.loc[df_position['account'] == trader, :].sort_values('openTimestamp')


id  \
7612  0x442b69937a0daf9d46439a71567fabe6cb69fbaf-0x1ec   
7617  0x442b69937a0daf9d46439a71567fabe6cb69fbaf-0x1f0   
7666  0x442b69937a0daf9d46439a71567fabe6cb69fbaf-0x21e   
5839  0x2b3bb4c683bfc5239b029131eef3b1d214478d93-0xcca   
5938  0x2b3bb4c683bfc5239b029131eef3b1d214478d93-0xd26   

                                         account asset  \
7612  0x1681cad31e305874b5a21396e40fa7dc170b2791    OP   
7617  0x1681cad31e305874b5a21396e40fa7dc170b2791    OP   
7666  0x1681cad31e305874b5a21396e40fa7dc170b2791    OP   
5839  0x1681cad31e305874b5a21396e40fa7dc170b2791  sETH   
5938  0x1681cad31e305874b5a21396e40fa7dc170b2791  sETH   

                  initialMargin size               entryPrice  \
7612   12132.811078139668205447    0     2.743680600844747876   
7617   19869.236359384337876648    0     2.754837589211131778   
7666   95382.491796858923487188    0     3.041291227243444658   
5839  116168.872917188009419644    0  1630.118304795638683008   
5938    44555.16705323421869018    0  1646.969809067382909424   

                avgEntryPrice                lastPrice  \
7612     2.743680600844747876     2.751664489714393578   
7617     2.754837589211131778     2.980229222807328583   
7666     3.041291227243444658     2.953902806694549706   
5839  1630.118304795638683008   1646.57617530541193378   
5938  1646.969809067382909424  1563.744085896039067759   

                    exitPrice                        pnl  ...  \
7612     2.751664489714393578     875.000091833533927965  ...   
7617     2.980229222807328583   28770.194800749874879936  ...   
7666     2.953902806694549706  -36484.850997685449922467  ...   
5839   1646.57617530541193378  -39130.812539714651669238  ...   
5938  1563.744085896039067759    -123.455336523814351751  ...   

                      feesPaid                netFunding isLiquidated isOpen  \
7612    758.614164081341760165     -8.649092571849980604        False  False   
7617   1004.370651815886884946   -752.138744990282332787        False  False   
7666   3448.634498715489397836  -3163.911932743271012393        False  False   
5839  12107.013580605613159124   -373.529045460285940088        False  False   
5938   1286.252212119276891873   -361.165336344812570958        False  False   

                        margin               netTransfers  \
7612  19871.236359384337876648    7628.688446064327502644   
7617  95384.491796858923487188   48499.570033530880051568   
7666    188.099589101318849271  -52098.994778613393347069   
5839     58.064836561033330559  -64501.452914846425324233   
5938    121.192112700406874622  -42665.102055545908001326   

                  totalDeposits                  totalVolume  \
7612    7628.688446064327502644    602266.331283440114914878   
7617   52862.570033530880051568    684936.196873252501376358   
7666  104071.878138574616072575     2713643.9030200802085693   
5839    3588.549712725441186117  15924289.640942608049046179   
5938    9748.320090512447413872   1647093.264403906723776101   

                                             lastTxHash  \
7612  0xb337cd37dd13c62361dacfb8d8c955ce0cffeba7359a...   
7617  0x3cd7087e09a823862ed38ea4c89c5d3ec0d2de69150f...   
7666  0x2b480c12abb5df0e6a68d062e30fb880d8f105441a40...   
5839  0x8a11a70fe3a2fe1e801ccfae29f1afaf7d0153e3979b...   
5938  0x46a411a7944992b807c39735397dacc698ce81bbf8fb...   

                         netPnl  
7612     116.385927752192167800  
7617   27765.824148933987994990  
7666  -39933.485496400939320303  
5839  -51237.826120320264828362  
5938   -1409.707548643091243624  

[5 rows x 23 columns]

## Plot market pnl over time

In [24]:
df_market_pnl = df_trade.sort_values(['asset', 'timestamp'])
df_market_pnl['netPnl'] = df_market_pnl['pnl'] - df_market_pnl['feesPaid']

df_market_pnl['timestamp'] = df_market_pnl['timestamp'].astype(np.int64)
df_market_pnl['pnl'] = df_market_pnl['pnl'].astype(np.float64)
df_market_pnl['netPnl'] = df_market_pnl['netPnl'].astype(np.float64)
df_market_pnl['feesPaid'] = df_market_pnl['feesPaid'].astype(np.float64)

df_market_pnl['pnl_cumulative'] = df_market_pnl.groupby('asset')['pnl'].cumsum()
df_market_pnl['feesPaid_cumulative'] = df_market_pnl.groupby('asset')['feesPaid'].cumsum()
df_market_pnl['netPnl_cumulative'] = df_market_pnl.groupby('asset')['netPnl'].cumsum()



In [25]:
fig = px.line(
    df_market_pnl,
    x='timestamp',
    y='pnl_cumulative',
    color='asset'
)
fig.show()

In [26]:
fig = px.line(
    df_market_pnl,
    x='timestamp',
    y='netPnl_cumulative',
    color='asset'
)
fig.show()


In [27]:
fig = px.line(
    df_market_pnl,
    x='timestamp',
    y='feesPaid_cumulative',
    color='asset'
)
fig.show()


In [28]:
df_market_pnl.to_csv('output/market_cumulative_pnl.csv', index=False)

In [29]:
df_market_pnl.groupby('asset')['netPnl'].sum().sort_values().reset_index().to_csv('output/market_pnl.csv', index=False)

## Do the same with position data

In [30]:
df_position_pnl = df_position[df_position['isOpen'] == False].sort_values(['asset', 'closeTimestamp'])
df_position_pnl['netPnl'] = df_position_pnl['pnl'] - df_position_pnl['feesPaid']

df_position_pnl['closeTimestamp'] = df_position_pnl['closeTimestamp'].astype(np.int64)
df_position_pnl['pnl'] = df_position_pnl['pnl'].astype(np.float64)
df_position_pnl['netPnl'] = df_position_pnl['netPnl'].astype(np.float64)
df_position_pnl['netFunding'] = df_position_pnl['netFunding'].astype(np.float64)

df_position_pnl['pnl_cumulative'] = df_position_pnl.groupby('asset')['pnl'].cumsum()
df_position_pnl['netPnl_cumulative'] = df_position_pnl.groupby('asset')['netPnl'].cumsum()
df_position_pnl['netFunding_cumulative'] = df_position_pnl.groupby('asset')['netFunding'].cumsum()



In [31]:
fig = px.line(
    df_position_pnl,
    x='closeTimestamp',
    y='pnl_cumulative',
    color='asset'
)
fig.show()


In [32]:
fig = px.line(
    df_position_pnl,
    x='closeTimestamp',
    y='netPnl_cumulative',
    color='asset'
)
fig.show()


In [33]:
fig = px.line(
    df_position_pnl,
    x='closeTimestamp',
    y='netFunding_cumulative',
    color='asset'
)
fig.show()


In [34]:
df_position_pnl['netPnl'].sum()

-2578477.191860499

In [35]:
df_position_pnl[df_position_pnl['asset'] == 'ATOM']['closeTimestamp'].min()

1675894747